In [1]:
from __windmodel3x3DBC__ import glob_all, save_models, WindLossmodel, define_composite_wind_model
from __windmodel3x3DBC__ import define_generator, define_discriminator, define_composite_model, train
from tensorflow.keras import backend as K

import warnings
warnings.filterwarnings('ignore')
import logging
logging.getLogger().disabled = True

import pandas as pd
import numpy as np
import tensorflow.compat.v1 as tf
import os

os.environ["CUDA_VISIBLE_DEVICES"] = "1"
tf.config.optimizer.set_jit(True)

In [2]:
resnet_n = 9 ; epochs = 500; batch = 1

home = '/media/disk3/weisting/CycleGan/Experiment5/'

dataA_norm = np.load('new_dataA_norm.npy')
dataB_norm = np.load('new_dataB_norm.npy')
print('Loaded', dataA_norm.shape, dataB_norm.shape)

EPA73_testing_PM25 = np.load(home+'348X204/EPA73_Testing_348X204_PM25.npy', mmap_mode='r')[:3000]


Train_Direc = np.concatenate([np.load('CWBEPA_Content_WIND_DIREC_graph_Training_K3.npy'),
                             np.load('CWBEPA_Content_WIND_DIREC_graph_Training_K3.npy')])

Train_Speed = np.concatenate([np.load('CWBEPA_Content_WIND_SPEED_graph_Training_K3.npy'),
                             np.load('CWBEPA_Content_WIND_SPEED_graph_Training_K3.npy')])

station_coordinate = pd.read_csv('RandomTesting/station_coordinate')
extract5_list = np.load('RandomTesting/extract5_list.npy')
extract10_list = np.load('RandomTesting/extract10_list.npy')
extract15_list = np.load('RandomTesting/extract15_list.npy')
extract20_list = np.load('RandomTesting/extract20_list.npy')

ex20_KNNhalf = np.load('ex20_KNN_half.npy', mmap_mode='r')
ex20_KNN_norm = np.load('ex20_KNN_norm.npy', mmap_mode='r')[:,:3000,:,:]

model_path = 'CWBEPA_Graph_RMSprop_Res'+str(resnet_n)+'_CycleGan_3x3DBwind/'
if not os.path.exists(model_path+'result/'):os.makedirs(model_path+'result/')

Loaded (3194, 348, 204, 1) (3194, 348, 204, 1)


In [ ]:
K.clear_session()
image_shape = dataB_norm[0].shape
g_model_AtoB = define_generator(image_shape,resnet_n)
print('generator: A -> B')
g_model_BtoA = define_generator(image_shape,resnet_n)
print('generator: B -> A')
d_model_A = define_discriminator(image_shape, d_lr=5e-5)
print('discriminator: A -> [real/fake]')
d_model_B = define_discriminator(image_shape, d_lr=5e-5)
print('discriminator: B -> [real/fake]')
c_model_AtoB = define_composite_model(g_model_AtoB, d_model_B, g_model_BtoA, image_shape, g_lr = 1e-3)
print('composite: A -> B -> [real/fake, A]')
c_model_BtoA = define_composite_model(g_model_BtoA, d_model_A, g_model_AtoB, image_shape, g_lr = 1e-3)
print('composite: B -> A -> [real/fake, B]')

WindLoss_model = WindLossmodel()
print('WindLoss_model')
c_model_wind = define_composite_wind_model(g_model_AtoB, WindLoss_model, image_shape, g_lr= 1e-5)
print('composite_wind_model')

train(d_model_A, d_model_B, g_model_AtoB, g_model_BtoA, c_model_AtoB, c_model_BtoA, c_model_wind,
      dataA_norm, dataB_norm, model_path, EPA73_testing_PM25, Train_Direc, Train_Speed,
      station_coordinate, extract5_list, extract10_list, extract15_list, extract20_list, ex20_KNN_norm, 
      ex20_KNNhalf, n_epochs=epochs, n_batch=batch, save_epochs = 1)

print('train models done')

generator: A -> B
generator: B -> A
discriminator: A -> [real/fake]
discriminator: B -> [real/fake]
composite: A -> B -> [real/fake, A]
composite: B -> A -> [real/fake, B]
WindLoss_model
composite_wind_model
3194
>00001, dALoss[0.955,2.145] dAAcc[0.561,0.393] dBLoss[1.021,1.808] dBAcc[0.254,0.493] g[22.319,22.011] wind[0.296]
>00002, dALoss[9.970,5.046] dAAcc[0.609,0.451] dBLoss[6.932,1.588] dBAcc[0.432,0.567] g[22.670,23.568] wind[0.257]
>00003, dALoss[1.667,3.372] dAAcc[0.596,0.482] dBLoss[1.816,4.177] dBAcc[0.478,0.697] g[28.639,19.794] wind[0.226]
>00004, dALoss[0.334,1.355] dAAcc[0.556,0.417] dBLoss[1.984,1.529] dBAcc[0.492,0.532] g[21.128,19.572] wind[0.120]
>00005, dALoss[0.225,0.942] dAAcc[0.670,0.449] dBLoss[0.760,1.796] dBAcc[0.382,0.608] g[23.522,19.704] wind[0.198]
>00006, dALoss[0.278,1.911] dAAcc[0.526,0.291] dBLoss[0.623,2.063] dBAcc[0.586,0.369] g[23.120,20.106] wind[0.168]
>00007, dALoss[0.285,1.635] dAAcc[0.612,0.706] dBLoss[1.247,0.969] dBAcc[0.563,0.660] g[22.275,20

>00071, dALoss[0.087,0.189] dAAcc[0.904,0.677] dBLoss[0.272,0.132] dBAcc[0.734,0.955] g[15.392,14.918] wind[0.253]
>00072, dALoss[0.062,0.058] dAAcc[0.931,0.906] dBLoss[0.138,0.066] dBAcc[0.859,0.845] g[14.194,13.953] wind[0.230]
>00073, dALoss[0.052,0.043] dAAcc[0.915,0.977] dBLoss[0.127,0.071] dBAcc[0.813,0.879] g[14.828,14.716] wind[0.223]
>00074, dALoss[0.171,0.148] dAAcc[0.736,0.661] dBLoss[0.127,0.176] dBAcc[0.914,0.843] g[15.525,14.933] wind[0.305]
>00075, dALoss[0.194,0.193] dAAcc[0.730,0.898] dBLoss[0.123,0.262] dBAcc[0.911,0.838] g[15.361,14.541] wind[0.228]
>00076, dALoss[0.194,0.248] dAAcc[0.731,0.768] dBLoss[0.107,0.256] dBAcc[0.957,0.826] g[17.501,16.497] wind[0.230]
>00077, dALoss[0.279,0.319] dAAcc[0.798,0.869] dBLoss[0.292,0.222] dBAcc[0.867,0.870] g[17.819,18.400] wind[0.290]
>00078, dALoss[0.362,0.280] dAAcc[0.632,0.750] dBLoss[0.213,0.169] dBAcc[0.658,0.887] g[13.880,13.802] wind[0.205]
>00079, dALoss[0.304,0.094] dAAcc[0.806,0.996] dBLoss[0.153,0.200] dBAcc[0.799,0

>00143, dALoss[0.118,0.023] dAAcc[0.934,0.978] dBLoss[0.073,0.051] dBAcc[0.904,0.938] g[15.290,15.421] wind[0.225]
>00144, dALoss[0.228,0.054] dAAcc[0.768,0.853] dBLoss[0.051,0.023] dBAcc[0.986,0.993] g[15.161,14.541] wind[0.282]
>00145, dALoss[0.086,0.124] dAAcc[0.930,0.904] dBLoss[0.056,0.026] dBAcc[0.962,0.983] g[15.154,16.730] wind[0.168]
>00146, dALoss[0.051,0.047] dAAcc[0.924,0.932] dBLoss[0.065,0.064] dBAcc[0.962,0.968] g[15.567,14.723] wind[0.222]
>00147, dALoss[0.018,0.009] dAAcc[0.990,1.000] dBLoss[0.201,0.058] dBAcc[0.938,0.957] g[15.855,14.878] wind[0.160]
>00148, dALoss[0.036,0.008] dAAcc[0.991,1.000] dBLoss[0.233,0.105] dBAcc[0.645,0.832] g[13.723,13.766] wind[0.184]
>00149, dALoss[0.054,0.030] dAAcc[0.842,0.928] dBLoss[0.130,0.147] dBAcc[0.777,0.962] g[11.109,10.826] wind[0.271]
>00150, dALoss[0.058,0.078] dAAcc[0.961,0.994] dBLoss[0.071,0.069] dBAcc[0.940,0.851] g[13.361,12.330] wind[0.281]
>00151, dALoss[0.054,0.046] dAAcc[0.982,0.913] dBLoss[0.040,0.007] dBAcc[0.921,0

>00215, dALoss[0.086,0.041] dAAcc[0.966,1.000] dBLoss[0.102,0.006] dBAcc[0.831,0.994] g[14.428,14.452] wind[0.214]
>00216, dALoss[0.039,0.049] dAAcc[0.942,0.935] dBLoss[0.208,0.041] dBAcc[0.767,0.910] g[13.106,12.759] wind[0.224]
>00217, dALoss[0.045,0.007] dAAcc[0.948,0.992] dBLoss[0.056,0.012] dBAcc[0.897,0.999] g[10.178,10.703] wind[0.155]
>00218, dALoss[0.164,0.066] dAAcc[0.652,1.000] dBLoss[0.019,0.004] dBAcc[0.999,0.999] g[11.925,10.749] wind[0.238]
>00219, dALoss[0.081,0.056] dAAcc[0.917,0.912] dBLoss[0.040,0.011] dBAcc[0.957,0.996] g[11.228,10.959] wind[0.253]
>00220, dALoss[0.051,0.006] dAAcc[0.893,0.993] dBLoss[0.033,0.017] dBAcc[0.961,1.000] g[12.124,11.690] wind[0.231]
>00221, dALoss[0.084,0.037] dAAcc[0.966,1.000] dBLoss[0.038,0.015] dBAcc[0.971,0.969] g[12.856,13.329] wind[0.263]
>00222, dALoss[0.085,0.028] dAAcc[0.922,0.942] dBLoss[0.039,0.012] dBAcc[0.952,1.000] g[13.388,13.478] wind[0.316]
>00223, dALoss[0.028,0.013] dAAcc[0.992,1.000] dBLoss[0.033,0.004] dBAcc[0.966,1

>00287, dALoss[0.064,0.013] dAAcc[0.945,0.960] dBLoss[0.012,0.015] dBAcc[0.987,1.000] g[12.418,12.653] wind[0.288]
>00288, dALoss[0.035,0.009] dAAcc[0.961,0.991] dBLoss[0.011,0.013] dBAcc[0.996,0.974] g[10.412,10.514] wind[0.170]
>00289, dALoss[0.022,0.021] dAAcc[1.000,1.000] dBLoss[0.019,0.026] dBAcc[0.991,0.988] g[12.500,11.742] wind[0.139]
>00290, dALoss[0.022,0.006] dAAcc[0.944,0.993] dBLoss[0.035,0.024] dBAcc[0.950,1.000] g[8.724,9.598] wind[0.285]
>00291, dALoss[0.022,0.005] dAAcc[1.000,1.000] dBLoss[0.050,0.010] dBAcc[0.990,1.000] g[11.804,11.576] wind[0.210]
>00292, dALoss[0.038,0.027] dAAcc[0.971,1.000] dBLoss[0.060,0.020] dBAcc[0.915,0.982] g[12.689,12.850] wind[0.270]
>00293, dALoss[0.040,0.018] dAAcc[0.982,0.959] dBLoss[0.035,0.050] dBAcc[0.975,1.000] g[10.605,10.709] wind[0.203]
>00294, dALoss[0.072,0.019] dAAcc[0.888,0.939] dBLoss[0.023,0.073] dBAcc[0.959,0.908] g[9.862,9.937] wind[0.185]
>00295, dALoss[0.043,0.048] dAAcc[0.995,1.000] dBLoss[0.016,0.016] dBAcc[1.000,1.000

...

>37990, dALoss[0.006,0.025] dAAcc[0.991,0.989] dBLoss[0.010,0.050] dBAcc[0.998,0.973] g[0.871,1.074] wind[0.308]
>37991, dALoss[0.004,0.006] dAAcc[0.999,1.000] dBLoss[0.014,0.100] dBAcc[0.999,0.730] g[0.925,1.824] wind[0.135]
>37992, dALoss[0.027,0.031] dAAcc[0.980,0.990] dBLoss[0.044,0.012] dBAcc[0.985,0.998] g[1.483,1.297] wind[0.210]
>37993, dALoss[0.012,0.021] dAAcc[1.000,1.000] dBLoss[0.058,0.052] dBAcc[0.931,0.957] g[1.559,2.481] wind[0.170]
>37994, dALoss[0.004,0.006] dAAcc[1.000,1.000] dBLoss[0.209,0.023] dBAcc[0.159,0.987] g[1.661,1.564] wind[0.204]
>37995, dALoss[0.008,0.006] dAAcc[1.000,1.000] dBLoss[0.013,0.027] dBAcc[1.000,0.984] g[1.054,1.515] wind[0.219]
>37996, dALoss[0.004,0.010] dAAcc[1.000,0.994] dBLoss[0.047,0.057] dBAcc[0.954,0.905] g[1.329,1.495] wind[0.220]
>37997, dALoss[0.026,0.027] dAAcc[0.995,0.997] dBLoss[0.040,0.014] dBAcc[0.969,0.998] g[1.732,1.856] wind[0.266]
>37998, dALoss[0.002,0.004] dAAcc[1.000,1.000] dBLoss[0.054,0.098] dBAcc[0.921,0.768] g[1.051,2.

>38063, dALoss[0.046,0.021] dAAcc[0.944,0.993] dBLoss[0.016,0.010] dBAcc[0.996,1.000] g[1.876,2.202] wind[0.157]
>38064, dALoss[0.005,0.006] dAAcc[1.000,1.000] dBLoss[0.013,0.018] dBAcc[0.993,1.000] g[1.553,1.354] wind[0.229]
>38065, dALoss[0.004,0.012] dAAcc[1.000,1.000] dBLoss[0.037,0.024] dBAcc[0.954,0.988] g[1.576,2.086] wind[0.159]
>38066, dALoss[0.022,0.009] dAAcc[1.000,1.000] dBLoss[0.110,0.007] dBAcc[0.642,1.000] g[1.834,1.297] wind[-0.072]
>38067, dALoss[0.019,0.032] dAAcc[0.998,0.999] dBLoss[0.011,0.045] dBAcc[1.000,0.945] g[1.159,1.693] wind[0.098]
>38068, dALoss[0.012,0.007] dAAcc[1.000,1.000] dBLoss[0.017,0.068] dBAcc[0.988,0.919] g[1.469,2.783] wind[0.179]
>38069, dALoss[0.003,0.006] dAAcc[1.000,0.999] dBLoss[0.009,0.013] dBAcc[0.992,0.982] g[1.484,1.678] wind[0.216]
>38070, dALoss[0.008,0.007] dAAcc[1.000,1.000] dBLoss[0.016,0.017] dBAcc[0.992,0.973] g[1.458,1.468] wind[0.160]
>38071, dALoss[0.030,0.054] dAAcc[0.998,0.943] dBLoss[0.077,0.024] dBAcc[0.881,0.990] g[1.583,1

>38136, dALoss[0.011,0.015] dAAcc[1.000,0.998] dBLoss[0.027,0.016] dBAcc[0.955,0.976] g[1.712,1.805] wind[0.118]
>38137, dALoss[0.004,0.014] dAAcc[1.000,0.986] dBLoss[0.025,0.030] dBAcc[0.989,0.988] g[0.964,1.542] wind[0.180]
>38138, dALoss[0.128,0.044] dAAcc[0.663,0.977] dBLoss[0.011,0.209] dBAcc[1.000,0.467] g[2.589,4.058] wind[0.290]
>38139, dALoss[0.004,0.006] dAAcc[1.000,1.000] dBLoss[0.023,0.017] dBAcc[1.000,0.998] g[1.634,1.834] wind[0.186]
>38140, dALoss[0.010,0.014] dAAcc[0.995,0.998] dBLoss[0.137,0.033] dBAcc[0.456,0.958] g[1.224,1.443] wind[0.177]
>38141, dALoss[0.006,0.006] dAAcc[1.000,1.000] dBLoss[0.009,0.012] dBAcc[0.998,0.998] g[1.497,2.031] wind[0.326]
>38142, dALoss[0.008,0.062] dAAcc[1.000,0.971] dBLoss[0.016,0.067] dBAcc[0.999,0.804] g[1.226,1.396] wind[0.368]
>38143, dALoss[0.013,0.042] dAAcc[1.000,1.000] dBLoss[0.041,0.011] dBAcc[0.970,1.000] g[1.655,2.537] wind[0.314]
>38144, dALoss[0.009,0.005] dAAcc[1.000,0.997] dBLoss[0.024,0.060] dBAcc[1.000,0.894] g[1.051,1.

>38209, dALoss[0.003,0.007] dAAcc[0.999,0.996] dBLoss[0.010,0.026] dBAcc[0.998,1.000] g[1.688,1.760] wind[0.245]
>38210, dALoss[0.145,0.038] dAAcc[0.407,0.991] dBLoss[0.019,0.013] dBAcc[0.993,0.998] g[1.601,1.733] wind[0.124]
>38211, dALoss[0.012,0.006] dAAcc[1.000,1.000] dBLoss[0.064,0.008] dBAcc[1.000,1.000] g[1.475,2.116] wind[0.203]
>38212, dALoss[0.022,0.010] dAAcc[1.000,1.000] dBLoss[0.016,0.039] dBAcc[0.995,1.000] g[1.936,1.682] wind[0.151]
>38213, dALoss[0.009,0.008] dAAcc[1.000,1.000] dBLoss[0.014,0.032] dBAcc[0.997,0.997] g[1.483,1.739] wind[0.152]
>38214, dALoss[0.007,0.019] dAAcc[1.000,1.000] dBLoss[0.190,0.021] dBAcc[0.256,1.000] g[2.049,1.618] wind[0.311]
>38215, dALoss[0.010,0.005] dAAcc[0.995,0.999] dBLoss[0.094,0.120] dBAcc[0.771,0.654] g[0.812,1.388] wind[0.342]
>38216, dALoss[0.006,0.007] dAAcc[1.000,1.000] dBLoss[0.013,0.032] dBAcc[1.000,0.973] g[1.432,2.015] wind[0.378]
>38217, dALoss[0.007,0.005] dAAcc[0.999,1.000] dBLoss[0.028,0.075] dBAcc[0.991,0.907] g[1.043,1.

>38282, dALoss[0.006,0.005] dAAcc[1.000,1.000] dBLoss[0.014,0.011] dBAcc[0.999,0.995] g[1.418,1.391] wind[0.180]
>38283, dALoss[0.003,0.010] dAAcc[1.000,0.995] dBLoss[0.009,0.024] dBAcc[1.000,0.991] g[1.650,2.089] wind[0.155]
>38284, dALoss[0.005,0.018] dAAcc[0.999,0.993] dBLoss[0.019,0.012] dBAcc[1.000,0.999] g[1.527,1.516] wind[0.118]
>38285, dALoss[0.006,0.006] dAAcc[1.000,1.000] dBLoss[0.038,0.010] dBAcc[0.995,1.000] g[1.927,1.868] wind[0.136]
>38286, dALoss[0.005,0.014] dAAcc[1.000,1.000] dBLoss[0.007,0.028] dBAcc[1.000,0.976] g[1.561,2.233] wind[0.124]
>38287, dALoss[0.004,0.027] dAAcc[0.999,0.993] dBLoss[0.018,0.009] dBAcc[0.977,0.998] g[1.653,1.184] wind[0.209]
>38288, dALoss[0.036,0.017] dAAcc[1.000,0.998] dBLoss[0.007,0.017] dBAcc[1.000,0.993] g[2.032,2.313] wind[0.186]
>38289, dALoss[0.007,0.006] dAAcc[1.000,1.000] dBLoss[0.026,0.020] dBAcc[0.995,0.986] g[1.130,1.491] wind[0.217]
>38290, dALoss[0.018,0.018] dAAcc[1.000,1.000] dBLoss[0.029,0.021] dBAcc[0.989,0.979] g[1.230,1.